In [8]:
from bokeh.plotting import figure, output_notebook, show
from bokeh.palettes import brewer
from bokeh.io import export_svgs
import numpy as np
import json

import scipy
import scipy.stats

output_notebook()

Loading BokehJS ...

In [128]:
with open("response/response.traj.json") as json_file:
    data = json.load(json_file)

In [57]:
limit = 100000
x = np.delete(data['timestamps'], np.s_[limit:], axis=0)
y = np.delete(data['components'], np.s_[limit:], axis=1)

In [129]:
data['random_variates']

[0.6711556372566626,
 0.5263824647815241,
 0.1567110838379522,
 0.21010773691133341,
 0.8701426349898582,
 0.6243118894964741,
 0.5622962702031545,
 0.3074232047003921,
 0.12665424491550847,
 0.3113531367425399,
 0.6993589241597112,
 0.9200237802736576,
 0.5687455365377037,
 0.5325737004181577,
 0.14206538065235655,
 0.47918993877220045,
 0.44046495065678554,
 0.4422540322496733,
 0.7760053130287958,
 0.38107340291388003,
 0.956876898822952,
 0.11830283808099157,
 0.0748668823414544,
 0.8361318113210413,
 0.011400783966736796,
 0.3571227092703354,
 0.0113896109069483,
 0.9010131008352142,
 0.8114609802556413,
 0.6247795126505341,
 0.5702159005161963,
 0.3134125749650276,
 0.5269503833106349,
 0.9826304303953184,
 0.748411608245966,
 0.7303966144744225,
 0.5561903736492637,
 0.8867245674964536,
 0.5603918672379341,
 0.9349621029319372,
 0.6865449618801239,
 0.9777209517844103,
 0.23895263657789584,
 0.1367151224532748,
 0.5030544889888415,
 0.29766707786833974,
 0.3865963835527161,
 0.5

In [135]:
reaction_events = np.array(data["reaction_events"])
reactants = np.choose(reaction_events, [reaction['reactants'][0] for reaction in data["reactions"]])

# for every reaction create an array that contains the propensity at every event
reaction_propensities = []
for reaction in data['reactions']:
    propensities = np.full(len(reaction_events), reaction['k'])
    for comp in reaction['reactants']:
        propensities *= np.array(data['components'][comp])

chosen_reaction_propensity = np.choose(reaction_events, reaction_propensities)
total_reaction_propensity = np.sum(reaction_propensities, axis=0)

# we want a list of the reactant concentration at every reaction event
reactant_concentrations = np.choose(reactants, [np.array(comp) for comp in data["components"]])
# we multiply it by the reaction constants and the time deltas
reaction_constants = np.choose(reaction_events, [reaction['k'] for reaction in data['reactions']])
time_deltas = np.diff(data['timestamps'], prepend=0)

transition_rates = reactant_concentrations * reaction_constants
survival_probabilities = np.array(data['random_variates'])

np.sum(np.log(transition_rates * survival_probabilities))

7196236.227370089

In [69]:
np.array(data["components"])

array([[10000.        , 10000.        , 10000.        , ...,
         6422.72432004,  6441.63457293,  6441.63457293],
       [ 8001.        ,  8002.        ,  8003.        , ...,
         6310.        ,  6311.        ,  6310.        ],
       [ 1000.        ,  1000.        ,  1000.        , ...,
         1386.        ,  1386.        ,  1386.        ]])

In [59]:
palette = brewer['Dark2'][8]

In [60]:
# create a new plot with a title and axis labels
p = figure(title="Trajectories", x_axis_label='t / s', y_axis_label='copies')

# add a line renderer with legend and line thickness
for y_value, col in zip(y, palette):
    p.step(x, y_value, line_width=2, color=col)

show(p)

In [ ]:
np.savetxt("tr2.txt", [x, y[1]])

In [ ]:
np.concatenate(([int_x], int_y), axis=0)

In [ ]:
p = figure()
p.line(int_x, int_y[0])
p.line(int_x, int_y[1])
show(p)

In [ ]:
hist = np.histogram(np.log(np.diff(txt_data[0])), bins='auto', density=True)
p=figure()
p.vbar(hist[1][:-1], width=np.diff(hist[1]), top=hist[0])
show(p)

In [ ]:
hist[0]

In [ ]:
np.loadtxt("tr2.txt").shape

In [ ]:
int_x

In [19]:
def ornstein_uhlenbeck_path(x0, t, mean_rev_speed, mean_rev_level, vola):
    """ Simulates a sample path for an Ornstein-Uhlenbeck process."""
    assert len(t) > 1
    x = scipy.stats.norm.rvs(size=len(t))
    x[0] = x0
    dt = np.diff(t)
    scale = std(dt, mean_rev_speed, vola)
    x[1:] = x[1:] * scale
    for i in range(1, len(x)):
        x[i] += mean(x[i - 1], dt[i - 1], mean_rev_speed, mean_rev_level)
    return x

def std(t, mean_rev_speed, vola):
    return np.sqrt(variance(t, mean_rev_speed, vola))

def variance(t, mean_rev_speed, vola):
    assert mean_rev_speed >= 0
    assert vola >= 0
    return vola * vola * (1.0 - np.exp(- 2.0 * mean_rev_speed * t)) / (2 * mean_rev_speed)

def mean(x0, t, mean_rev_speed, mean_rev_level):
    assert mean_rev_speed >= 0
    return x0 * np.exp(-mean_rev_speed * t) + (1.0 - np.exp(- mean_rev_speed * t)) * mean_rev_level

In [20]:
times = np.linspace(0, 100, 100000)
x = ornstein_uhlenbeck_path(10000, times, 0.001, 10000, 900)
p = figure()
p.line(times, x)
show(p)

In [27]:
json_obj = { 'timestamps': times.tolist(), 'components': [x.tolist()] }
with open("response/ouproc.txt", "w") as outfile:
    json.dump(json_obj, outfile)